# Лабораторная работа #9: Введение в NLP

## Импорт библиотек

In [ ]:
import nltk
nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from sklearn.datasets import load_files
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, accuracy_score
import re
from datasets import load_dataset
import pandas as pd
import spacy
from nltk.stem.snowball import SnowballStemmer
from sklearn.datasets import load_files
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report
import re

import warnings
warnings.filterwarnings("ignore")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## Базовые методы работы с текстом

Данная глава должна наглядно показать, как обработать простейший текст с помощью разных методов

Первый доступный нам способ обработки строк – посимвольная замена. Вы её уже видели много раз (в том числе на ЕГЭ, там str.replace точно применяется). Следующий этап – [регулярные выражения](https://ru.wikipedia.org/wiki/%D0%A0%D0%B5%D0%B3%D1%83%D0%BB%D1%8F%D1%80%D0%BD%D1%8B%D0%B5_%D0%B2%D1%8B%D1%80%D0%B0%D0%B6%D0%B5%D0%BD%D0%B8%D1%8F). Её и используем для удаления лишних символов (не букв, знаков пунктуации в нашем случае), а также лишних пробелов:

In [ ]:
def clean_text(t):
    t = t.lower()
    t = re.sub(r"<.*?>", " ", t)
    t = re.sub(r"[^a-z ]", " ", t)
    t = re.sub(r"\s+", " ", t).strip()
    return t

Можно пойти дальше, и удалить целые слова. Действительно, некоторые слова служат исключительно для связки и не несут никакой семантики, болтаясь балластом. Это так называемые "стоп-слова": разнообразные артикли, частицы, вводные слова и союзы. Их список можно достать средствами nltk.stopwords. Дальше их очень просто удалить. Одна проблема: нам нужна не строка, а список слов. Об этом пойдёт речь дальше.

In [ ]:
def remove_stopwords(t):
  filtered_words = []
  for word in t:
    if word in set(stopwords.words('english')):
        continue
    filtered_words.append(word)
  return filtered_words

Продолжаем рост сложности. Теперь используем библиотеку spaCy для токенизации и лемматизации, а также SnowBallStemmer из библиотеки nltk для стемминга.

Краткое напоминание:
1. Токенизация – разбиение текста на слова, предложения или другие единицы (токены). Грубо говоря, строку делим на массив строк (как метод split).

2. Лемматизация – приведение слова к словарной форме (лемме) с учётом контекста и морфологии (`fading -> fade`)

3. Стемминг - грубое отсечение окончаний и суффиксов для приведения слова к базовой форме (`location -> locat`).

Подробнее можно было узнать на лекции... ну или в интернете: [Токенизация](https://ru.wikipedia.org/wiki/%D0%9B%D0%B5%D0%BA%D1%81%D0%B8%D1%87%D0%B5%D1%81%D0%BA%D0%B8%D0%B9_%D0%B0%D0%BD%D0%B0%D0%BB%D0%B8%D0%B7), [Лемматизация](https://ru.wikipedia.org/wiki/%D0%9B%D0%B5%D0%BC%D0%BC%D0%B0%D1%82%D0%B8%D0%B7%D0%B0%D1%86%D0%B8%D1%8F), [Стемминг](https://ru.wikipedia.org/wiki/%D0%A1%D1%82%D0%B5%D0%BC%D0%BC%D0%B8%D0%BD%D0%B3).

In [ ]:
nlp = spacy.load("en_core_web_sm")
stemmer = SnowballStemmer("english")

В качестве примера возьмём выборку из 5 кратких текстов на английском языке. Тексты взяты из датасета [UFO Sightings](https://www.kaggle.com/datasets/NUFORC/ufo-sightings/data)

In [ ]:
texts = [
  "Bright white light&#44 dissapearing and reappearing in different locations in the night sky&#44 eventually dissapearing&#44 fading away.",
  "Six orange orbs plague the skies of Publix in Davie.",
  "Strange noises",
  "SAW TWO SMALL 3-4 FOOT TRIANGULAR SHAPED DULL METALIC OBJECTS BELOW THE CLOUDS MOVING IN A SYNCRONIZED MANNER  ROLLING END OVER END AN",
  "Glowing moon-sized object moves across the sky&#44 only to leave an orange streak behind it before it dissapears."
]
texts

['Bright white light&#44 dissapearing and reappearing in different locations in the night sky&#44 eventually dissapearing&#44 fading away.',
 'Six orange orbs plague the skies of Publix in Davie.',
 'Strange noises',
 'SAW TWO SMALL 3-4 FOOT TRIANGULAR SHAPED DULL METALIC OBJECTS BELOW THE CLOUDS MOVING IN A SYNCRONIZED MANNER  ROLLING END OVER END AN',
 'Glowing moon-sized object moves across the sky&#44 only to leave an orange streak behind it before it dissapears.']

Возьмём первый текст. Почистим его регуляркой:

In [ ]:
text = clean_text(texts[0])
text

'bright white light dissapearing and reappearing in different locations in the night sky eventually dissapearing fading away'

Вытащим информацию о токене, лемму и стем:

In [ ]:
document = nlp(text)
for token in document:
  print(f"TOKEN: {token.text}; LEMMA: {token.lemma_}; STEM: {stemmer.stem(token.lemma_)}")

TOKEN: bright; LEMMA: bright; STEM: bright
TOKEN: white; LEMMA: white; STEM: white
TOKEN: light; LEMMA: light; STEM: light
TOKEN: dissapearing; LEMMA: dissapeare; STEM: dissapear
TOKEN: and; LEMMA: and; STEM: and
TOKEN: reappearing; LEMMA: reappear; STEM: reappear
TOKEN: in; LEMMA: in; STEM: in
TOKEN: different; LEMMA: different; STEM: differ
TOKEN: locations; LEMMA: location; STEM: locat
TOKEN: in; LEMMA: in; STEM: in
TOKEN: the; LEMMA: the; STEM: the
TOKEN: night; LEMMA: night; STEM: night
TOKEN: sky; LEMMA: sky; STEM: sky
TOKEN: eventually; LEMMA: eventually; STEM: eventu
TOKEN: dissapearing; LEMMA: dissapeare; STEM: dissapear
TOKEN: fading; LEMMA: fade; STEM: fade
TOKEN: away; LEMMA: away; STEM: away


Соберём стемы в отдельный список:

In [ ]:
removed_stopwords = remove_stopwords([token.text for token in document]) # beware, now this is a list of strings, not tokens!!!
final_tokens = [stemmer.stem(word) for word in removed_stopwords]
result = " ".join(final_tokens)
result

'bright white light dissapear reappear differ locat night sky eventu dissapear fade away'

In [ ]:
# TODO: Токенизировать, удалить стоп-слова, провести лемматизацию и стемминг других 4-х строк из массива texts

Теперь попытаемся преобразовать полученный список токенов к численному виду (так называемый Embedding, математический вектор чисел). Есть множество подходов к решению этой задачи. Выделим два из них: Bag-of-words и TF-IDF. Краткое пояснение к методам:
1. Bag-of-words. Массив слов преобразуется в массив частот слов. Размер массива такой, сколько слов в тексте (или в целевых данных, можно хоть все слова русского языка брать, тогда будет массив длины 100 тыс. и больше). Прост для понимания, но размерность получаемого пространства ужасающе огромная
2. TF-IDF. Вместо частоты встречи слова считает метрики TF (Term Frequency, частота слова в текущем документе) и IDF (Inverse Document Frequency, обратная частота слова среди всех документов). Они перемножаются, и получается, что слова, которые во всех текстах встречаются, получают маленький вес, а редкие и специфичные для одного документа – большой. Отсекая слова с маленьким весом, можно значительно уменьшить размерность пространства.

Подробнее было на лекции, или в интернете: [Bag-of-words](https://en.wikipedia.org/wiki/Bag-of-words_model), [TF-IDF](https://ru.wikipedia.org/wiki/TF-IDF).

Метод Bag-of-Words реализуем с помощью CountVectorizer из sklearn (он нас теперь преследует), TF-IDF с помощью TfidfVectorizer оттуда же.

Будьте осторожны: CountVectorizer и TfidfVectorizer принимают на вход в fit_transform набор строк, а не набор массивов строк. Поэтому финальные токены придётся join-ить через пробел...

In [ ]:
cvec = CountVectorizer(max_features=20000)
final_tokens_cnt = cvec.fit_transform([' '.join(final_tokens)])
cvec.vocabulary_

{'bright': np.int64(1),
 'white': np.int64(11),
 'light': np.int64(6),
 'dissapear': np.int64(3),
 'reappear': np.int64(9),
 'differ': np.int64(2),
 'locat': np.int64(7),
 'night': np.int64(8),
 'sky': np.int64(10),
 'eventu': np.int64(4),
 'fade': np.int64(5),
 'away': np.int64(0)}

In [ ]:
print(final_tokens_cnt)

<Compressed Sparse Row sparse matrix of dtype 'int64'
	with 12 stored elements and shape (1, 12)>
  Coords	Values
  (0, 1)	1
  (0, 11)	1
  (0, 6)	1
  (0, 3)	2
  (0, 9)	1
  (0, 2)	1
  (0, 7)	1
  (0, 8)	1
  (0, 10)	1
  (0, 4)	1
  (0, 5)	1
  (0, 0)	1


Как это прочитать: во втором принте у нас значения: в CountVectorizer частота, в TF-IDF - значение TF*IDF. Из координат берёте второе значение, ищете его в словаре, оно соответствует слову.

In [ ]:
tfidf = TfidfVectorizer(max_features=20000)
final_tokens_tfidf = tfidf.fit_transform([' '.join(final_tokens)])
tfidf.vocabulary_

{'bright': np.int64(1),
 'white': np.int64(11),
 'light': np.int64(6),
 'dissapear': np.int64(3),
 'reappear': np.int64(9),
 'differ': np.int64(2),
 'locat': np.int64(7),
 'night': np.int64(8),
 'sky': np.int64(10),
 'eventu': np.int64(4),
 'fade': np.int64(5),
 'away': np.int64(0)}

In [ ]:
print(final_tokens_tfidf)

<Compressed Sparse Row sparse matrix of dtype 'float64'
	with 12 stored elements and shape (1, 12)>
  Coords	Values
  (0, 1)	0.2581988897471611
  (0, 11)	0.2581988897471611
  (0, 6)	0.2581988897471611
  (0, 3)	0.5163977794943222
  (0, 9)	0.2581988897471611
  (0, 2)	0.2581988897471611
  (0, 7)	0.2581988897471611
  (0, 8)	0.2581988897471611
  (0, 10)	0.2581988897471611
  (0, 4)	0.2581988897471611
  (0, 5)	0.2581988897471611
  (0, 0)	0.2581988897471611


## Практическое задание

Работать нужно будет с датасетом отзывов IMDB. Он содержит два столбца: текст отзыва и бинарная оценка (положительный/отрицательный). Задача: по тексту отзыва предсказать, положительный он или отрицательный.

Логика, соответствующая обучению классификаторов, уже написана за вас.

От вас требуется предобработать столбец с отзывами так, чтобы он превратился из текста в численный (каждому отзыву сопоставить Embedding, вектор чисел). Следует сделать это двумя способами: CountVectorizer и TF-IDF. Не забудьте про токенизацию, лемматизацию, стемминг. Функциями для обработки пробелов и не-букв регулярками, а также удаление стоп-слов можно подхватить из примеров выше.

In [ ]:
NSAMPLES = 20 # Change for larger dataframe. Beware: lemmatization will take forever! (╥﹏╥)

In [ ]:
ds = load_dataset("stanfordnlp/imdb")
ds = pd.concat([pd.DataFrame(ds["train"]), pd.DataFrame(ds["test"])]).sample(NSAMPLES)
X, y = ds["text"], ds["label"]

In [ ]:
# TODO: предобработка X. Можно делать сколько угодно новых ячеек здесь, не обязательно делать в одной

# Для классификаторов нужно 2 набора:
# X_train_countvect, X_test_countvect, y_train, y_test
# X_train_tfidf, X_test_tfidf, y_train, y_test
# Совет: fit_transform и transform для train и test можно делать уже после train_test_split
# Так удобнее, чем постоянно держать в голове два набора

In [ ]:
model = LogisticRegression(max_iter=200)
model.fit(X_train_countvect, y_train)
y_pred = clf_count.predict(X_test_countvect)
print("CountVectorizer Accuracy:", accuracy_score(y_test, y_pred))

CountVectorizer Accuracy: 0.25


In [ ]:
print("Bag-of-words Classification Report:")
print(classification_report(y_test, y_pred, target_names=["neg", "pos"]))

In [ ]:
model = LogisticRegression(max_iter=200)
model.fit(X_train_tfidf, y_train)
pred_tfidf = clf_tfidf.predict(X_test_tfidf)
print("TfidfVectorizer Accuracy:", accuracy_score(y_test, pred_tfidf))

TfidfVectorizer Accuracy: 0.5


In [ ]:
print("TF-IDF Classification Report:")
print(classification_report(y_test, pred_tfidf, target_names=["neg", "pos"]))



TF-IDF Classification Report:
              precision    recall  f1-score   support

         neg       0.50      1.00      0.67         2
         pos       0.00      0.00      0.00         2

    accuracy                           0.50         4
   macro avg       0.25      0.50      0.33         4
weighted avg       0.25      0.50      0.33         4

